### Класс, описывающий состояние

In [30]:
import numpy as np
import itertools
import matplotlib.pyplot as plt
from sympy import symbols, Matrix, zeros, init_printing, Rational
from copy import copy, deepcopy
import pickle
########################################################

class Condition():

    def __init__(self, y, i, n_los, n_nlos):
        self.y = y
        self.i = i
        self.n_los = n_los
        self.n_nlos = n_nlos
        self.probability = 0
        self.is_blocking = False
        self.id = hash(self)

        self.hide_matrices = False

    def __hash__(self):
        return hash((
            self.y.tobytes(),
            self.i.tobytes(),
            self.n_los.tobytes(),
            self.n_nlos.tobytes()
        ))
    
    def __eq__(self, other):
        # if not isinstance(other, Condition):
        #     return False
        # return (
        #     np.array_equal(self.i, other.i) and
        #     np.array_equal(self.y, other.y) and
        #     np.array_equal(self.n_los, other.n_los) and
        #     np.array_equal(self.n_nlos, other.n_nlos)
        # )
        return hash(self) == hash(other)

    def __repr__(self):
        if self.hide_matrices:
            return f"id: {self.id}\nprobability: {self.probability}\nis blocking?: {self.is_blocking} \n"
        return f"id: {self.id}\ny: {self.y}\ni: {self.i}\nn los: {self.n_los}\nn nlos: {self.n_nlos} \nprobability: {self.probability}\nis blocking?: {self.is_blocking} \n"

### Функция постройки пространства состояний Z и записывания Z в текстовый файл

In [31]:
def construct_Z_space(R, M, L, K, b_los, b_nlos, d_los, d_nlos):
    Z = []
    
    for y in itertools.product([0, 1], repeat=M*L):
        y_matrix = np.array(y).reshape(M, L)

        for i in itertools.product([0, 1], repeat=M*L):
            i_matrix = np.array(i).reshape(M, L)
            
            if np.any((y_matrix == 0) & (i_matrix == 1)):
                continue

            for n_los in itertools.product(*[range(int(R / d_los[k][l]) + 1) for k in range(K) for l in range(L)]):
                n_LoS_matrix = np.array(n_los).reshape(K, L)
                
                for n_nlos in itertools.product(*[range(int(R / d_nlos[k][l]) + 1) for k in range(K) for l in range(L)]):
                    n_nlos_matrix = np.array(n_nlos).reshape(K, L)
                    
                    total_resource = 0

                    for m in range(M):
                        max_bl = 0
                        for l in range(L):
                            bl = y_matrix[m][l] * b_los[m][l] + i_matrix[m][l] * (b_nlos[m][l] - b_los[m][l])
                            if bl > max_bl:
                                max_bl = bl
                        total_resource += max_bl
                

                    for k in range(K):
                        for l in range(L):
                            total_resource += n_LoS_matrix[k][l] * d_los[k][l] + n_nlos_matrix[k][l] * d_nlos[k][l]
                    
                    if total_resource <= R:
                        cnd = Condition(y_matrix, i_matrix, n_LoS_matrix, n_nlos_matrix)
                        print("matr: ", y_matrix, i_matrix, n_LoS_matrix, n_nlos_matrix)
                        print("sost: ", cnd.y, cnd.i, cnd.n_los, cnd.n_nlos)
                        Z.append(cnd)
    
    matrix_name = ["Y", "I", "N_LoS", "N_nLoS"]
    with open("matrices.txt", "w") as f:  
        i = 0
        for z in Z:
            i = i + 1
            f.write(f"Z_{i}:\n")
            j = 0            
            for matrix in [z.y, z.i, z.n_los, z.n_nlos]:
                name = matrix_name[j]
                f.write(f"\t{name}: ")
                for array in matrix:
                    f.write(f"{array}\t")
                f.write("\n")
                j = j + 1
            f.write("\n\n")
    print(f"SMATRI TUT {Z}")
    return Z

### Функция постройки матрицы переходов по хешам (""""экспериментально"""")

In [33]:
def construct_transition_matrix(  z_all,
                    lambda_I, lambda_II, 
                    mu_I,  mu_II, 
                    theta_I_in, theta_I_out,  
                    sigma_II_in, sigma_II_out, 
                    R, 
                    b_los, b_nlos, 
                    d_los, d_nlos,
                    M, L, K
                    ):
    
    matrix = zeros(len(z_all), len(z_all))
    for index, z in enumerate(z_all):

        y, i, n_los, n_nlos = [z.y, z.i, z.n_los, z.n_nlos]

        r = 0
        for m in range(M):
            max_bl = 0
            for l in range(L):
                bl = y[m][l] * b_los[m][l] + i[m][l] * (b_nlos[m][l] - b_los[m][l])
                if bl > max_bl:
                    max_bl = bl
            r += max_bl
        
        for k in range(K):
            for l in range(L):
                r += n_los[k][l] * d_los[k][l] + n_nlos[k][l] * d_nlos[k][l]
        

        for l in range(L):
            for m in range(M):
                lambda_I_ml = lambda_I[m, l]
                mu_I_ml = mu_I[m, l]
                theta_in_ml = theta_I_in[m, l]
                theta_out_ml = theta_I_out[m, l]
                y_ml = y[m][l]
                i_ml = i[m][l]
                b_los_ml = b_los[m][l]
                b_nlos_ml = b_nlos[m][l]

                for k in range(K):
                    lambda_II_kl = lambda_II[k, l]
                    mu_II_kl = mu_II[k, l]
                    sigma_in_kl = sigma_II_in[k, l]
                    sigma_out_kl = sigma_II_out[k, l]
                    n_los_kl = n_los[k][l]
                    n_nlos_kl = n_nlos[k][l]
                    d_los_kl = d_los[k][l]
                    d_nlos_kl = d_nlos[k][l]

                    I1 = (r + d_los_kl <= R)
                    I2 = (y_ml == 0 and i_ml == 0 and r + b_los_ml <= R)
                    I3 = (y_ml == 1 and i_ml == 0)
                    I4 = (y_ml == 1 and i_ml == 0 and r + (b_nlos_ml - b_los_ml) <= R)
                    I5 = (y_ml == 1 and i_ml == 1)
                    I6 = (y_ml == 1)
                    I7 = (y_ml == 0 and i_ml == 0)
                    I8 = (n_nlos_kl > 0)
                    I9 = (n_los_kl > 0 and r + (d_nlos_kl - d_los_kl) <= R)
                    I10 = I8
                    I11 = (r + d_nlos_kl <= R)
                    I12 = (n_los_kl > 0)

                    for inner_index, inner_array in enumerate(z_all):

                        if inner_index == index:
                            continue

                        
                        ### КРАСНАЯ СТРЕЛКА (особый казус)

                        if I7:
                            copied_z = deepcopy(z)
                            copied_z.y[m][l] = 1
                            copied_z.i[m][l] = 0
                            if copied_z == inner_array:
                                diff = z.y - inner_array.y
                                diff_non_zero = np.count_nonzero(diff)
                                z_y_non_zero = np.count_nonzero(z.y)
                                if z_y_non_zero == 0:
                                    if I2:
                                        matrix[index, inner_index] = matrix[index, inner_index] + lambda_I_ml
                                elif diff_non_zero > 0 and z_y_non_zero > 0:
                                    summed = z.y + diff
                                    row, col = np.argwhere(summed == -1)[0]
                                    row_elements = summed[row, :]  
                                    left_of_neg1 = row_elements[:col]
                                    has_1_left = np.any(left_of_neg1 == 1)
                                    right_of_neg1 = row_elements[col + 1 :]
                                    has_1_right = np.any(right_of_neg1 == 1)

                                    if has_1_right and r<=R:
                                        matrix[index, inner_index] = matrix[index, inner_index] + lambda_I_ml
                                    
                                    if has_1_left:
                                        _max = 0
                                        for _l in range(L):
                                            result = y[m][_l]*b_los[m][_l] + i[m][_l]*(b_nlos[m][_l] - b_los[m][_l])
                                            if _max < result:
                                                _max = result
                                        if r+(b_los_ml - _max) <= R:
                                            matrix[index, inner_index] = matrix[index, inner_index] + lambda_I_ml
                            
                        ### ОРАНЖЕВАЯ СТРЕЛКА (особый казус №2)
                            
                        if i_ml == 0:
                            copied_z = deepcopy(z)
                            copied_z.y[m][l] = 1
                            copied_z.i[m][l] = 1
                            if copied_z == inner_array:
                                #matrix[index, inner_index] = matrix[index, inner_index] +  theta_in_ml
                                diff = z.i - inner_array.i
                                diff_non_zero = np.count_nonzero(diff)
                                z_y_non_zero = np.count_nonzero(z.i)
                                if z_y_non_zero == 0:
                                    if I4:
                                        matrix[index, inner_index] = matrix[index, inner_index] + theta_in_ml
                                elif diff_non_zero > 0 and z_y_non_zero > 0:
                                    summed = z.i + diff
                                    row, col = np.argwhere(summed == -1)[0]
                                    row_elements = summed[row, :]  
                                    left_of_neg1 = row_elements[:col] 
                                    has_1_left = np.any(left_of_neg1 == 1)
                                    right_of_neg1 = row_elements[col + 1 :] 
                                    has_1_right = np.any(right_of_neg1 == 1)

                                    if has_1_right and r<=R and y_ml == 1:
                                        matrix[index, inner_index] = matrix[index, inner_index] + theta_in_ml
                                    
                                    if has_1_left and y_ml == 1:
                                        _max = 0
                                        for _l in range(L):
                                            result = y[m][_l]*b_los[m][_l] + i[m][_l]*(b_nlos[m][_l] - b_los[m][_l])
                                            if _max < result:
                                                _max = result
                                        if r+(b_los_ml - _max) <= R:
                                            matrix[index, inner_index] = matrix[index, inner_index] + theta_in_ml
                            
                        if I5:
                            copied_z = deepcopy(z)
                            copied_z.y[m][l] = 1
                            copied_z.i[m][l] = 0
                            if copied_z == inner_array:
                                matrix[index, inner_index] = matrix[index, inner_index] +  theta_out_ml
                        if I6:
                            copied_z = deepcopy(z)
                            copied_z.y[m][l] = 0
                            copied_z.i[m][l] = 0
                            if copied_z == inner_array:
                                matrix[index, inner_index] = matrix[index, inner_index] +  mu_I_ml
                        
                        # -------------------------------------------
                        
                        if I8:
                            copied_z = deepcopy(z)
                            copied_z.n_los[k][l] = n_los_kl+1
                            copied_z.n_nlos[k][l] = n_nlos_kl-1
                            if copied_z == inner_array:
                                matrix[index, inner_index] = matrix[index, inner_index] +  sigma_out_kl
                        if I9:
                            copied_z = deepcopy(z)
                            copied_z.n_los[k][l] = n_los_kl-1
                            copied_z.n_nlos[k][l] = n_nlos_kl+1
                            if copied_z == inner_array:
                                matrix[index, inner_index] = matrix[index, inner_index] +  sigma_in_kl
                        if I10:
                            copied_z = deepcopy(z)
                            copied_z.n_nlos[k][l] = n_nlos_kl-1
                            if copied_z == inner_array:
                                matrix[index, inner_index] = matrix[index, inner_index] +  n_nlos_kl*mu_II_kl
                        if I12:
                            copied_z = deepcopy(z)
                            copied_z.n_los[k][l] = n_los_kl-1
                            if copied_z == inner_array:
                                matrix[index, inner_index] = matrix[index, inner_index] +  n_los_kl*mu_II_kl     
                        if I1:
                            copied_z = deepcopy(z)
                            copied_z.n_los[k][l] = n_los_kl+1
                            if copied_z == inner_array:
                                matrix[index, inner_index] = matrix[index, inner_index] +  lambda_II_kl

        matrix[index, index] = -sum(matrix[index, :])

    # y_s = np.zeros(shape=(len(z_all)))
    # y_s[-1] = 1 

    # matrix = matrix.transpose()
    # matrix[-1] = np.ones(shape=(len(z_all)))

    # result = np.linalg.solve(matrix, y_s)
    return matrix

### Функция нахождения предельных вероятностей

In [34]:
def calculate_probabilities(transition_matrix, shape, substitutes):
    b = Matrix.zeros(shape, 1)
    b[-1] = 1

    coeffs = transition_matrix.subs(substitutes)
    coeffs[-1, :] = Matrix([[1] * coeffs.cols])

    coeffs_np = np.array(coeffs).astype(float)
    b_np = np.array(b).astype(float)

    probabilities = np.linalg.solve(coeffs_np, b_np)

    return probabilities

### Функция приписывания вероятности к состоянию

In [35]:
def attach_probabilities_to_conditions(probabilities, z):
    for probability, condition in zip(probabilities, z):
        condition.probability = probability[0]

### Функция рассчёта множества блокировки доступа для многоадресных соединений в состоянии прямой видимости

In [36]:
def b_I_los(z_all, R, b_los, b_nlos, d_los, d_nlos, fixed_m, fixed_l, M, L, K):
    blockers = []
    for z in z_all:
        y, i, n_los, n_nlos = [z.y, z.i, z.n_los, z.n_nlos]
        if y[fixed_m][fixed_l] == 0:
            sum_1 = 0
            for m in range(M):
                _max = 0
                for l in range(L):
                    result = y[m][l]*b_los[m][l] + i[m][l]*(b_nlos[m][l] - b_los[m][l])
                    if result > _max:
                        _max = result
                sum_1 = sum_1 + _max
            sum_2 = 0
            for k in range(K):
                for l in range(L):
                    sum_2 = (sum_2 +
                            n_los[k][l] * d_los[k][l] + n_nlos[k][l] * d_nlos[k][l])
            sum_3 = 0 
            _max = 0
            for l in range(L):
                result = (y[fixed_m][l]*b_los[fixed_m][l] 
                        + i[fixed_m][l]*(b_nlos[fixed_m][l] - b_los[fixed_m][l]))
                if result > _max:
                    _max = result
            sum_3 = b_los[fixed_m][fixed_l] - _max
            if sum_1 + sum_2 + sum_3 > R:
                z.is_blocking = True
                blockers.append(z)
    return blockers

### Функция рассчёта множества блокировки доступа для многоадресных соединений в состоянии нарушения прямой видимости

In [37]:
def b_I_nlos(z_all, R, b_los, b_nlos, d_los, d_nlos, fixed_m, fixed_l, M, L, K):
    blockers = []
    for z in z_all:
        y, i, n_los, n_nlos = [z.y, z.i, z.n_los, z.n_nlos]
        if y[fixed_m][fixed_l] == 1 and i[fixed_m][fixed_l] == 0:
            sum_1 = 0
            for m in range(M):
                _max = 0
                for l in range(L):
                    result = y[m][l]*b_los[m][l] + i[m][l]*(b_nlos[m][l] - b_los[m][l])
                    if result > _max:
                        _max = result
                sum_1 = sum_1 + _max
            sum_2 = 0
            for k in range(K):
                for l in range(L):
                    sum_2 = (sum_2 +
                            n_los[k][l] * d_los[k][l] + n_nlos[k][l] * d_nlos[k][l])
            sum_3 = 0 
            _max = 0
            for l in range(L):
                result = (y[fixed_m][l]*b_los[fixed_m][l] 
                        + i[fixed_m][l]*(b_nlos[fixed_m][l] - b_los[fixed_m][l]))
                if result > _max:
                    _max = result
            sum_3 = b_nlos[fixed_m][fixed_l] - _max
            if sum_1 + sum_2 + sum_3 > R:
                z.is_blocking = True
                blockers.append(z)
    return blockers

### Функция рассчёта множества блокировки доступа для одноадресных соединений в состоянии прямой видимости

In [38]:
def b_II_los(z_all, R, b_los, b_nlos, d_los, d_nlos, fixed_k, fixed_l, M, L, K):
    blockers = []
    for i, z in enumerate(z_all):
        y, i, n_los, n_nlos = [z.y, z.i, z.n_los, z.n_nlos]
        sum_1 = 0
        for m in range(M):
            _max = 0
            for l in range(L):
                result = y[m][l]*b_los[m][l] + i[m][l]*(b_nlos[m][l] - b_los[m][l])
                if result > _max:
                    _max = result
            sum_1 = sum_1 + _max
        sum_2 = 0
        for k in range(K):
            for l in range(L):
                sum_2 = (sum_2 +
                         n_los[k][l] * d_los[k][l] + n_nlos[k][l] * d_nlos[k][l])
        sum_3 = d_los[fixed_k][fixed_l]
        if sum_1 + sum_2 + sum_3 > R:
            z.is_blocking = True
            blockers.append(z)
    return blockers

### Функция рассчёта множества блокировки доступа для одноадресных соединений в состоянии нарушения прямой видимости

In [39]:
def b_II_nlos(z_all, R, b_los, b_nlos, d_los, d_nlos, fixed_k, fixed_l, M, L, K):
    blockers = []
    for z in z_all:
        y, i, n_los, n_nlos = [z.y, z.i, z.n_los, z.n_nlos]
        if n_los[fixed_k][fixed_l] > 0:
            sum_1 = 0
            for m in range(M):
                _max = 0
                for l in range(L):
                    result = y[m][l]*b_los[m][l] + i[m][l]*(b_nlos[m][l] - b_los[m][l])
                    if result > _max:
                        _max = result
                sum_1 = sum_1 + _max
            sum_2 = 0
            for k in range(K):
                for l in range(L):
                    sum_2 = (sum_2 +
                            n_los[k][l] * d_los[k][l] + n_nlos[k][l] * d_nlos[k][l])
            sum_3 = d_nlos[fixed_k][fixed_l] -  d_los[fixed_k][fixed_l]
            if sum_1 + sum_2 + sum_3 > R:
                z.is_blocking = True
                blockers.append(z)
    return blockers

### Функция рассчёта всех множеств блокировки

In [40]:
def b_formulas(z_all, R, b_los, b_nlos, d_los, d_nlos, M, L, K):
    b_I_los_ml = []
    b_I_nlos_ml = []
    b_II_los_ml = []
    b_II_nlos_ml = []
    
    b_I_los_separate = []
    b_II_los_separate = []

    b_I_nlos_separate = []
    b_II_nlos_separate = []

    for m in range(M):
        for l in range(L):
            blockers = b_I_los(z_all, R, b_los, b_nlos, d_los, d_nlos, m, l, M, L, K)
            b_I_los_ml = b_I_los_ml + blockers
            b_I_los_separate.append((f"{m+1}{l+1}", blockers))

    for m in range(M):
        for l in range(L):
            blockers = b_I_nlos(z_all, R, b_los, b_nlos, d_los, d_nlos, m, l, M, L, K)
            b_I_nlos_ml = b_I_nlos_ml + blockers
            b_I_nlos_separate.append((f"{m+1}{l+1}", blockers))

    for k in range(K):
        for l in range(L):
            blockers = b_II_los(z_all, R, b_los, b_nlos, d_los, d_nlos, k, l, M, L, K)
            b_II_los_ml = b_II_los_ml + blockers
            b_II_los_separate.append((f"{k+1}{l+1}", blockers))

    for k in range(K):
        for l in range(L):
            blockers = b_II_nlos(z_all, R, b_los, b_nlos, d_los, d_nlos, k, l, M, L, K)
            b_II_nlos_ml = b_II_nlos_ml + blockers
            b_II_nlos_separate.append((f"{k+1}{l+1}", blockers))

    b_I_los_ml = set(b_I_los_ml)
    b_I_nlos_ml = set(b_I_nlos_ml)
    b_II_los_ml = set(b_II_los_ml)
    b_II_nlos_ml = set(b_II_nlos_ml)


  
    b_I = b_I_los_ml.union(b_I_nlos_ml)
    b_II = b_II_los_ml.union(b_II_nlos_ml)

    return (b_I_los_ml, b_I_nlos_ml, b_I, b_II_los_ml, b_II_nlos_ml, b_II, b_I_los_separate, b_II_los_separate, b_I_nlos_separate, b_II_nlos_separate)

### Функции для рассчёта потребления ресурса (всё в одну ячейку так как они довольно ёмкие)

In [41]:
def r_u(K, L, D_LoS, D_nLoS, probs, z_all):
    sums = []
    for index, prob in enumerate(probs):
        _sum = 0
        for k in range(K):
            for l in range(L):
                _sum = _sum + (z_all[index].n_los[k][l] * D_LoS[k][l] +
                               z_all[index].n_nlos[k][l] * D_nLoS[k][l])
        _sum = _sum * prob
        sums.append(_sum)
    return sum(sums)

def r_m(M, L, B_LoS, B_nLoS, probs, z_all):
    sums = []
    for index, prob in enumerate(probs):
        _sum = 0
        for m in range(M):
            _max = 0
            for l in range(L):
                result = (z_all[index].y[m][l] * B_LoS[m][l]
                          + z_all[index].i[m][l] * (B_nLoS[m][l] - B_LoS[m][l]))
                if result > _max:
                    _max = result
            #print(_max)
            _sum = _sum + _max
        print(f"Сумма для состояния {index+1}: {_sum}; вероятность: {prob}")
        sums.append(_sum*prob)
    return sum(sums)

def r(M, K, L, B_LoS, B_nLoS, D_LoS, D_nLoS, probs, z_all):
    sums = []
    for index, prob in enumerate(probs):
        _sum = 0
        for m in range(M):
            _max = 0
            for l in range(L):
                result = (z_all[index].y[m][l] * B_LoS[m][l]
                          + z_all[index].i[m][l] * (B_nLoS[m][l] - B_LoS[m][l]))
                if result > _max:
                    _max = result
            _sum = _sum + _max
        for k in range(K):
            for l in range(L):
                _sum = _sum + (z_all[index].n_los[k][l] * D_LoS[k][l] +
                               z_all[index].n_nlos[k][l] * D_nLoS[k][l])
        sums.append(_sum*prob)
    return sum(sums)

### Ниже идёт подготовка аргументов для программы и собсна говоря её исполнение

In [28]:
R = Rational(953.67)
M = 2
L = 2
K = 1
B_LoS = [
    [Rational(137.7), Rational(275.4)],
    [Rational(206.55), Rational(413.1)],
]


B_nLoS = [
    [Rational(275.4), Rational(550.8)],
    [Rational(413.1), Rational(826.2)],
]

D_LoS = [
    [Rational(33.47), Rational(100.41)],
]

D_nLoS = [
    [Rational(100.41), Rational(301.23)],
]

lambda_11_I, lambda_12_I, lambda_21_I, lambda_22_I, lambda_11_II, lambda_12_II = symbols('lambda_11_I lambda_12_I lambda_21_I lambda_22_I lambda_11_II lambda_12_II')
mu_11_I, mu_12_I, mu_21_I, mu_22_I, mu_11_II, mu_12_II = symbols('mu_11_I mu_12_I mu_21_I mu_22_I mu_11_II mu_12_II')
theta_11_I_in, theta_12_I_in, theta_21_I_in, theta_22_I_in, theta_11_I_out, theta_12_I_out, theta_21_I_out, theta_22_I_out = symbols('theta_11_I_in theta_12_I_in theta_21_I_in theta_22_I_in theta_11_I_out theta_12_I_out theta_21_I_out theta_22_I_out')
sigma_11_II_in, sigma_12_II_in, sigma_11_II_out, sigma_12_II_out = symbols('sigma_11_II_in sigma_12_II_in sigma_11_II_out sigma_12_II_out')

Lambda_I = Matrix([[lambda_11_I, lambda_12_I],[lambda_21_I, lambda_22_I]])
Lambda_II = Matrix([[lambda_11_II, lambda_12_II]])

Mu_I = Matrix([[mu_11_I, mu_12_I],[mu_21_I, mu_22_I]])
Mu_II = Matrix([[mu_11_II, mu_12_II]])

Theta_I_in = Matrix([[theta_11_I_in, theta_12_I_in], [theta_21_I_in, theta_22_I_in]])
Theta_I_out = Matrix([[theta_11_I_out, theta_12_I_out],[theta_21_I_out, theta_22_I_out]])

Sigma_II_in = Matrix([[sigma_11_II_in, sigma_12_II_in]])
Sigma_II_out = Matrix([[sigma_11_II_out, sigma_12_II_out]])


substitute = {
    mu_11_I:15,
    mu_12_I:15,
    mu_21_I:15,
    mu_22_I:15,
    mu_11_II:30,
    mu_12_II:30,
    theta_11_I_in:4,
    theta_12_I_in:4,
    theta_21_I_in:4,
    theta_22_I_in:4,
    theta_11_I_out:Rational(1.25),
    theta_12_I_out:Rational(1.25),
    theta_21_I_out:Rational(1.25),
    theta_22_I_out:Rational(1.25),
    sigma_11_II_in:4,
    sigma_12_II_in:4,
    sigma_11_II_out:Rational(1.25),
    sigma_12_II_out:Rational(1.25)
}

In [42]:
R = Rational(953.67)
M = 2
L = 2
K = 1
B_LoS = [
    [Rational(137.7), Rational(413.1)],
    [Rational(206.55), Rational(619.65)],
]


B_nLoS = [
    [Rational(192.78), Rational(578.34)],
    [Rational(289.17), Rational(867.51)],
]

D_LoS = [
    [Rational(33.47), Rational(100.41)],
]

D_nLoS = [
    [Rational(100.41), Rational(301.23)],
]

lambda_11_I, lambda_12_I, lambda_21_I, lambda_22_I, lambda_11_II, lambda_12_II = symbols('lambda_11_I lambda_12_I lambda_21_I lambda_22_I lambda_11_II lambda_12_II')
mu_11_I, mu_12_I, mu_21_I, mu_22_I, mu_11_II, mu_12_II = symbols('mu_11_I mu_12_I mu_21_I mu_22_I mu_11_II mu_12_II')
theta_11_I_in, theta_12_I_in, theta_21_I_in, theta_22_I_in, theta_11_I_out, theta_12_I_out, theta_21_I_out, theta_22_I_out = symbols('theta_11_I_in theta_12_I_in theta_21_I_in theta_22_I_in theta_11_I_out theta_12_I_out theta_21_I_out theta_22_I_out')
sigma_11_II_in, sigma_12_II_in, sigma_11_II_out, sigma_12_II_out = symbols('sigma_11_II_in sigma_12_II_in sigma_11_II_out sigma_12_II_out')

Lambda_I = Matrix([[lambda_11_I, lambda_12_I],[lambda_21_I, lambda_22_I]])
Lambda_II = Matrix([[lambda_11_II, lambda_12_II]])

Mu_I = Matrix([[mu_11_I, mu_12_I],[mu_21_I, mu_22_I]])
Mu_II = Matrix([[mu_11_II, mu_12_II]])

Theta_I_in = Matrix([[theta_11_I_in, theta_12_I_in], [theta_21_I_in, theta_22_I_in]])
Theta_I_out = Matrix([[theta_11_I_out, theta_12_I_out],[theta_21_I_out, theta_22_I_out]])

Sigma_II_in = Matrix([[sigma_11_II_in, sigma_12_II_in]])
Sigma_II_out = Matrix([[sigma_11_II_out, sigma_12_II_out]])


substitute = {
    mu_11_I:15,
    mu_12_I:15,
    mu_21_I:15,
    mu_22_I:15,
    mu_11_II:30,
    mu_12_II:30,
    theta_11_I_in:4,
    theta_12_I_in:4,
    theta_21_I_in:4,
    theta_22_I_in:4,
    theta_11_I_out:Rational(1.25),
    theta_12_I_out:Rational(1.25),
    theta_21_I_out:Rational(1.25),
    theta_22_I_out:Rational(1.25),
    sigma_11_II_in:4,
    sigma_12_II_in:4,
    sigma_11_II_out:Rational(1.25),
    sigma_12_II_out:Rational(1.25)
}

In [43]:
Z = construct_Z_space(R, M, L, K, B_LoS, B_nLoS, D_LoS, D_nLoS)


matr:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[0 0]]
sost:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[0 0]]
matr:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[0 1]]
sost:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[0 1]]
matr:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[0 2]]
sost:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[0 2]]
matr:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[0 3]]
sost:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[0 3]]
matr:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[1 0]]
sost:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[1 0]]
matr:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[1 1]]
sost:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[1 1]]
matr:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[1 2]]
sost:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[1 2]]
matr:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[2 0]]
sost:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[2 0]]
matr:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[2 1]]
sost:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [[2 1]]
matr:  [[0 0]
 [0 0]] [[0 0]
 [0 0]] [[0 0]] [

In [15]:
transition_matrix = 0
with open('pickled_matrix.pkl', 'rb') as f:
    transition_matrix = pickle.load(f)
    print(len(transition_matrix))

46185616


### Выводим состояния блокаторы для многоадрес и одноадрес, каждое кольцо

In [16]:
B_M_LoS_array, B_M_nLoS_array,B_M_array, B_U_LoS_array, B_U_nLoS_array, B_U_array, sep1, sep2, sep3, sep4 = b_formulas(Z, R, B_LoS, B_nLoS, D_LoS, D_nLoS, M, L, K)
print(B_M_LoS_array)
print("##########################")
print(B_M_nLoS_array)
print("#########################")
print(sep1)
print("#########################")
print(sep3)
print("#########################")
print(B_U_LoS_array)
print("##########################")
print(B_U_nLoS_array)
print("#########################")
print(sep2)
print("#########################")
print(sep4)

{id: -606747730531057664
y: [[0 0]
 [1 1]]
i: [[0 0]
 [0 1]]
n los: [[3 0]]
n nlos: [[0 0]] 
probability: 0
is blocking?: True 
, id: -4424310528144670710
y: [[1 1]
 [0 0]]
i: [[1 0]
 [0 0]]
n los: [[1 1]]
n nlos: [[0 2]] 
probability: 0
is blocking?: True 
, id: -7398658204723970034
y: [[0 0]
 [1 1]]
i: [[0 0]
 [1 0]]
n los: [[2 0]]
n nlos: [[0 1]] 
probability: 0
is blocking?: True 
, id: -4316261904107503599
y: [[1 0]
 [1 0]]
i: [[0 0]
 [0 0]]
n los: [[4 3]]
n nlos: [[0 0]] 
probability: 0
is blocking?: True 
, id: -103943195132821486
y: [[1 0]
 [0 0]]
i: [[0 0]
 [0 0]]
n los: [[3 0]]
n nlos: [[0 4]] 
probability: 0
is blocking?: True 
, id: -6932927718522716137
y: [[0 0]
 [0 0]]
i: [[0 0]
 [0 0]]
n los: [[5 0]]
n nlos: [[0 4]] 
probability: 0
is blocking?: True 
, id: 3086720381948919838
y: [[1 0]
 [0 0]]
i: [[0 0]
 [0 0]]
n los: [[3 1]]
n nlos: [[2 0]] 
probability: 0
is blocking?: True 
, id: -7205179521205567456
y: [[0 1]
 [0 0]]
i: [[0 1]
 [0 0]]
n los: [[0 2]]
n nlos: [[0 2]] 